In [1]:
#Liberías para tablas
import numpy as np
import pandas as pd
pd.set_option("display.max_columns",1000)
pd.set_option("display.max_rows",1000)

# ----------------------------------------------------------------------------------------------------------

#Librerías gráficas
import matplotlib.pyplot as plt
plt.style.use("ggplot") # to make matplotlib look better
%matplotlib inline
import seaborn as sns
import plotly
from plotly import graph_objs as go
import plotly.express as px
from plotly.offline import download_plotlyjs, init_notebook_mode,  iplot
from plotly.subplots import make_subplots
init_notebook_mode(connected=True)
BKCF_colors = ['#e32592','#fae700','#34b233','#58585a','#939597','#E0E1DD','#5bcbf5','#fe4540','#c7be71'] # to use with cufflinks
layout = go.Layout(colorway=BKCF_colors) # to use with plain plotly
import cufflinks as cf
cf.set_config_file(offline=True)
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True) # to allow plotly offline for jupyter notebooks
import pandas_bokeh
pandas_bokeh.output_notebook()
from bokeh.plotting import save # to allow saving pandas bokeh plots into html files
from IPython.core.display import display, HTML
display(HTML(
    '<style>'
        '#notebook { padding-top:0px !important; } ' 
        '.container { width:90% !important; } '
        '.end_space { min-height:0px !important; } '
    '</style>'
))
# ----------------------------------------------------------------------------------------------------------

#Dash
from jupyter_dash import JupyterDash
import dash
import dash_core_components as dcc
import dash_html_components as html
from dash.dependencies import Input, Output,State

#Ipywidgets
import ipywidgets as widgets
from ipywidgets import interact, interact_manual

#Otras
import yfinance as yf
from datetime import date
import calendar
import pickle
import sys,os
from varname import nameof
from scipy import stats
import operator
import calendar
from scipy.stats import norm
from scipy import stats
#import statsmodels.api as sm
import pylab
from ipywidgets import widgets
import warnings
warnings.filterwarnings('ignore')
import datetime
import os

C:\Users\Javier\Anaconda3\lib\site-packages\statsmodels\tools\_testing.py:19: FutureWarning: pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.
  import pandas.util.testing as tm


Loading BokehJS ...

# Functions

In [2]:
#Save in pickle format
def save_obj(obj, name, path="./obj"):
    if not(os.path.isdir(path)):
        os.mkdir(path)
        print("Creado directorio './obj' donde guardar objeto")
    with open("{}/{}.pkl".format(path,name), "wb") as f:
        pickle.dump(obj, f, pickle.HIGHEST_PROTOCOL)
        
#Load a pickle        
def load_obj(name, path="./obj"):
    with open("{}/{}.pkl".format(path, name), "rb") as f:
        return pickle.load(f)

def download_data(my_list):
    for i in range(0,len(my_list)):
        df = yf.Ticker(my_list[i]).history(period="max").reset_index().drop(columns=['Dividends','Stock Splits'])
        df.name = my_list[i]
        save_obj(df,df.name)
        
#Week prices
def week_prices(df):
    df_aux = df.copy()
    df_aux['Day_of_week']= pd.to_datetime(df_aux['Date']).dt.dayofweek
    df_aux['Month']= pd.DatetimeIndex(df_aux['Date']).month
    df_aux['Year']= pd.DatetimeIndex(df_aux['Date']).year
    df_week = df_aux[df_aux['Day_of_week']==4][['Date','Open','High','Low','Close','Volume']].reset_index()
    return df_week

#Month prices
def month_prices(df):
    df_aux = df.copy()
    df_aux['Month']= pd.DatetimeIndex(df_aux['Date']).month
    df_aux['Year']= pd.DatetimeIndex(df_aux['Date']).year
    df_month = pd.DataFrame(df_aux.groupby(['Year','Month'])[['Date','Open','High','Low','Close','Volume']].agg('first')).reset_index()
    return df_month

#Year prices
def year_prices(df,start_date,final_date):
    df_aux = df.copy()
    df_aux['Year']= pd.DatetimeIndex(df_aux['Date']).year
    df_start_date = df_aux[df_aux['Date']==start_date][['Year','Date','Open','High','Low','Close','Volume']]
    df_final_date = df_aux[df_aux['Date']==final_date][['Year','Date','Open','High','Low','Close','Volume']]
    df_year = pd.DataFrame(df_aux.groupby(['Year'])[['Date','Open','High','Low','Close','Volume']].agg('last')).reset_index()
    df_year = pd.concat([df_start_date,df_year,df_final_date]).sort_values(by="Date")
    df_year = df_year[(df_year['Date']<=final_date)&(df_year['Date']>=start_date)]
    return df_year

#Download info stock
def download_data(my_list):
    for i in range(0,len(my_list)):
        df = yf.Ticker(my_list[i]).history(period="max").reset_index().drop(columns=['Dividends','Stock Splits'])
        df.name = my_list[i]
        save_obj(df,df.name)
    return df

####################### Double axis #####################################
def double_axis(plot1,plot2,title,x_label,left_y_label,right_y_label,number_of_traces):
    fig = make_subplots(specs=[[{"secondary_y": True}]])

    # Add traces
    for i in range(0,number_of_traces):
        fig.add_trace(plot1.data[i],secondary_y=False)
        fig.add_trace(plot2.data[i],secondary_y=True)

    # Add figure title
    fig.update_layout(title_text = title)

    # Set x-axis title
    fig.update_xaxes(title_text = x_label)

    # Set y-axes titles
    fig.update_yaxes(title_text = left_y_label, secondary_y=False)
    fig.update_yaxes(title_text = right_y_label, secondary_y=True)
    fig.show()

In [3]:
#Portolio information
def portfolio_return(company_list,company_names, company_weighs, initial_investment, 
                     start_date, final_date,benchmark_list,benchmark_names):
    
    #Select the maximum min date from all dataframes
    min_dates = []
    for company in company_list:
        min_dates.append(company['Date'].min())
    fecha_minima_comun = max(min_dates)

    company_list_1 = []
    for company in company_list:
        company = company[company['Date']>=fecha_minima_comun]
        company_list_1.append(company)
    
    company_return_all = company_list_1[0][['Date']]
    indice = -1
    for company in company_list_1:
        indice = indice + 1
        company['Price'] =  company['Close']
        company['Volume'] = company['Volume']
        company['Return'] = company['Close'].pct_change()
        company = company.dropna()
        company.name = company_names[indice]
        company_return = company[['Date','Price','Volume','Return']].rename(columns={'Return':'Return'+'_'+ company.name,
                                                                           'Price':'Price'+'_'+ company.name,
                                                                            'Volume':'Volume'+'_'+ company.name        })
        company_return = company_return[(company_return['Date']>=start_date) & (company_return['Date']<=final_date)]
        company_return.index = range(company_return.shape[0])
        company_return_all = company_return_all.merge(company_return,on="Date")
        
         #Accumulated return
        company_return_all['Investment_acumulado_{0}'.format(company.name)] = initial_investment*company_weighs[indice]
        for i in range(1,company_return_all.shape[0]):
            company_return_all['Investment_acumulado_{0}'.format(company.name)][i] = company_return_all['Investment_acumulado_{0}'.format(company.name)][i-1]*(1+company_return_all['Return_{0}'.format(company.name)][i-1])
    
    indice = -1
    for company in company_list_1:
        indice = indice + 1
        company.name = company_names[indice]
        
    #Investment acumulado total
    company_return_all['Investment_acumulado_total'] = company_return_all['Investment_acumulado_{0}'.format(company_list_1[0].name)]
    for i in range (1, len(company_list_1)): 
        company_return_all['Investment_acumulado_total'] = company_return_all['Investment_acumulado_total']+company_return_all['Investment_acumulado_{0}'.format(company_list_1[i].name)]
   
    #Percentage of allocation
    for company in company_list_1:  
        company_return_all['Percentage_allocation_{0}'.format(company.name)] = company_return_all['Investment_acumulado_{0}'.format(company.name)]/company_return_all['Investment_acumulado_total']
     
    #Day return total
    company_return_all['Return_total'] = company_return_all['Return_{0}'.format(company_list_1[0].name)]*company_return_all['Percentage_allocation_{0}'.format(company_list_1[0].name)]
    for i in range (1, len(company_list_1)): 
        company_return_all['Return_total'] = company_return_all['Return_total']+company_return_all['Return_{0}'.format(company_list_1[i].name)]*company_return_all['Percentage_allocation_{0}'.format(company_list_1[i].name)]
    
    #Drawdawns
    for i in range(0,len(company_names)):
        company_return_all['Previous_peak_{0}'.format(company_names[i])] = company_return_all['Investment_acumulado_{0}'.format(company_names[i])].cummax()
        company_return_all['Drawdawn_{0}'.format(company_names[i])] = (company_return_all['Investment_acumulado_{0}'.format(company_names[i])] - company_return_all['Previous_peak_{0}'.format(company_names[i])])/company_return_all['Previous_peak_{0}'.format(company_names[i])]
    company_return_all = company_return_all.loc[:, company_return_all.columns.str.contains('peak')==False]
    
    #Month and year
    company_return_all['Month'] = pd.DatetimeIndex(company_return_all['Date']).month
    company_return_all['Year'] = pd.DatetimeIndex(company_return_all['Date']).year
    company_return_all['Day'] = pd.DatetimeIndex(company_return_all['Date']).dayofyear
    company_return_all['Day_of_week']= pd.to_datetime(company_return_all['Date']).dt.dayofweek
    dictionary = {0: "Lunes", 1: "Martes", 2:"Miercoles",3:"Jueves",4:"Viernes"}
    company_return_all['Day_of_week'].replace(dictionary, inplace=True)
    
    #Change order of columns 
    cols = company_return_all.columns.tolist()
    cols = cols[-3:] + cols[:-3]
    company_return_all = company_return_all[cols]
    
    
    
    #Benchmark
    benchmark_return_all = benchmark_list[0][['Date']]
    benchmark_return_all = benchmark_return_all[benchmark_return_all['Date']>=company_return_all['Date'].min()]
    indice = -1
    for benchmark in benchmark_list:
        indice = indice + 1
        benchmark['Price'] = benchmark['Close']
        benchmark['Volume'] = benchmark['Volume']
        benchmark['Return'] = benchmark['Close'].pct_change()
        benchmark = benchmark.dropna()
        benchmark.name = benchmark_names[indice]
        print(benchmark.name)
        benchmark_return = benchmark[['Date','Price','Volume','Return']].rename(columns={'Return':'Benchmark_return'+'_'+ benchmark.name,
                                                                               'Price':'Benchmark_price'+'_'+ benchmark.name,
                                                                               'Volume':'Benchmark_volume'+'_'+ benchmark.name         })
        benchmark_return = benchmark_return[(benchmark_return['Date']>=start_date) & (benchmark_return['Date']<=final_date)]
        benchmark_return.index = range(benchmark_return.shape[0])
        benchmark_return_all = benchmark_return_all.merge(benchmark_return,on="Date")
        
         #Accumulated return
        benchmark_return_all['Benchmark_investment_acumulado_{0}'.format(benchmark.name)] = initial_investment
        for i in range(1,benchmark_return_all.shape[0]):
            benchmark_return_all['Benchmark_investment_acumulado_{0}'.format(benchmark.name)][i] = benchmark_return_all['Benchmark_investment_acumulado_{0}'.format(benchmark.name)][i-1]*(1+benchmark_return_all['Benchmark_return_{0}'.format(benchmark.name)][i-1])
    
    indice = -1
    for benchmark in benchmark_list:
        indice = indice + 1
        benchmark.name = benchmark_names[indice]
        
    #Drawdawns
    for i in range(0,len(benchmark_names)):
        benchmark_return_all['Previous_peak_{0}'.format(benchmark_names[i])] = benchmark_return_all['Benchmark_price_{0}'.format(benchmark_names[i])].cummax()
        benchmark_return_all['Benchmark_drawdawn_{0}'.format(benchmark_names[i])] = (benchmark_return_all['Benchmark_price_{0}'.format(benchmark_names[i])] - benchmark_return_all['Previous_peak_{0}'.format(benchmark_names[i])])/benchmark_return_all['Previous_peak_{0}'.format(benchmark_names[i])]
    benchmark_return_all = benchmark_return_all.loc[:, benchmark_return_all.columns.str.contains('peak')==False]
    
    benchmark_return_all = company_return_all.merge(benchmark_return_all)
    return benchmark_return_all


##########Tabla########################
def tabla(day_returns,week_returns,month_returns,year_returns,company_names):
    feature_list = ['Stock','Day_return_mean_arithmetic','Day_return_mean_geometric','Day_return_stdev','Day_return_stdev_downside','Day_return_skewness','Day_return_excess_kurtosis','Day_best','Day_worst','Day_max_drawdawn','Day_historical_VaR','Day_gaussian_VaR','Day_cornish-fisher_VaR','Day_CVaR',
                    'Month_return_mean_arithmetic','Month_return_mean_geometric','Month_return_stdev','Month_return_stdev_downside','Month_return_skewness','Month_return_excess_kurtosis','Month_best','Month_worst','Month_max_drawdawn','Month_historical_VaR','Month_gaussian_VaR','Month_cornish-fisher_VaR','Month_CVaR',
                    'Year_return_mean_arithmetic','Year_return_mean_geometric','Year_return_stdev','Year_return_stdev_downside','Year_return_skewness','Year_return_excess_kurtosis','Year_best','Year_worst','Year_max_drawdawn','Year_historical_VaR','Year_gaussian_VaR','Year_cornish-fisher_VaR','Year_CVaR','Sharpe_ratio','Sortino_ratio',
                   'Beta','Alpha','Treynor_ratio','Calmar_ratio','Active_return','Tracking_error','Information_ratio',
                   '%Day_up','%Week_up','%Month_up','%Year_up']
    
    tabla = pd.DataFrame(0.00, index=np.arange(len(company_names)), columns=feature_list)
    
    #Daily volatility
    for i in range(0,len(company_names)):
        tabla['Stock'][i] = company_names[i]
        
        #Day
        tabla['Day_return_mean_arithmetic'][i] = day_returns['Return_{0}'.format(company_names[i])].mean()
        tabla['Day_return_mean_geometric'][i] = day_returns['Return_{0}'.format(company_names[i])].add(1).prod()**(1/day_returns.shape[0])-1
        tabla['Day_return_stdev'][i] = day_returns['Return_{0}'.format(company_names[i])].std()
        tabla['Day_return_stdev_downside'][i] = day_returns['Return_{0}'.format(company_names[i])].where(day_returns['Return_{0}'.format(company_names[i])] < 0).std()
        tabla['Day_return_skewness'][i] = day_returns['Return_{0}'.format(company_names[i])].skew()
        tabla['Day_return_excess_kurtosis'][i] = day_returns['Return_{0}'.format(company_names[i])].kurtosis()-3
        tabla['Day_best'][i] = day_returns['Return_{0}'.format(company_names[i])].max()
        tabla['Day_worst'][i] = day_returns['Return_{0}'.format(company_names[i])].min()
        tabla['Day_max_drawdawn'][i] = day_returns['Drawdawn_{0}'.format(company_names[i])].min()
        tabla['Day_historical_VaR'][i] = day_returns['Return_{0}'.format(company_names[i])].quantile(0.05)
        tabla['Day_gaussian_VaR'][i] = tabla['Day_return_mean_arithmetic'][i] + norm.ppf(0.05)*tabla['Day_return_stdev'][i]
        z = norm.ppf(0.05)
        s = tabla['Day_return_skewness'][i]
        k = tabla['Day_return_excess_kurtosis'][i]+3
        z = (z + (z**2 - 1)*s/6 + (z**3 -3*z)*(k-3)/24 -(2*z**3 - 5*z)*(s**2)/36)
        tabla['Day_cornish-fisher_VaR'][i] = tabla['Day_return_mean_arithmetic'][i] + z*tabla['Day_return_stdev'][i]
        tabla['Day_CVaR'][i] = day_returns['Return_{0}'.format(company_names[i])].where(day_returns['Return_{0}'.format(company_names[i])] < tabla['Day_cornish-fisher_VaR'][i]).mean()
        
        #Month
        tabla['Month_return_mean_arithmetic'][i] = month_returns['Return_{0}'.format(company_names[i])].mean()
        tabla['Month_return_mean_geometric'][i] = month_returns['Return_{0}'.format(company_names[i])].add(1).prod()**(1/month_returns.shape[0])-1
        tabla['Month_return_stdev'][i] = month_returns['Return_{0}'.format(company_names[i])].std()
        tabla['Month_return_stdev_downside'][i] = month_returns['Return_{0}'.format(company_names[i])].where(month_returns['Return_{0}'.format(company_names[i])] < 0).std()
        tabla['Month_return_skewness'][i] = month_returns['Return_{0}'.format(company_names[i])].skew()
        tabla['Month_return_excess_kurtosis'][i] = month_returns['Return_{0}'.format(company_names[i])].kurtosis()-3
        tabla['Month_best'][i] = month_returns['Return_{0}'.format(company_names[i])].max()
        tabla['Month_worst'][i] = month_returns['Return_{0}'.format(company_names[i])].min()
        tabla['Month_max_drawdawn'][i] = month_returns['Drawdawn_{0}'.format(company_names[i])].min()
        tabla['Month_historical_VaR'][i] = month_returns['Return_{0}'.format(company_names[i])].quantile(0.05)
        tabla['Month_gaussian_VaR'][i] = tabla['Month_return_mean_arithmetic'][i] + norm.ppf(0.05)*tabla['Month_return_stdev'][i] 
        z = norm.ppf(0.05)
        s = tabla['Month_return_skewness'][i]
        k = tabla['Month_return_excess_kurtosis'][i]+3
        z = (z + (z**2 - 1)*s/6 + (z**3 -3*z)*(k-3)/24 -(2*z**3 - 5*z)*(s**2)/36)
        tabla['Month_cornish-fisher_VaR'][i] = tabla['Month_return_mean_arithmetic'][i] + z*tabla['Month_return_stdev'][i]
        tabla['Month_CVaR'][i] = month_returns['Return_{0}'.format(company_names[i])].where(month_returns['Return_{0}'.format(company_names[i])] < tabla['Month_cornish-fisher_VaR'][i]).mean()
        
        #Year
        tabla['Year_return_mean_arithmetic'][i] = (1+tabla['Month_return_mean_arithmetic'][i])**12-1
        tabla['Year_return_mean_geometric'][i] = (1+tabla['Month_return_mean_geometric'][i])**12-1
        tabla['Year_return_stdev'][i] = tabla['Month_return_stdev'][i]*np.sqrt(12)
        tabla['Year_return_stdev_downside'][i] = tabla['Month_return_stdev_downside'][i]*np.sqrt(12)
        tabla['Year_return_skewness'][i] = year_returns['Return_{0}'.format(company_names[i])].skew()
        tabla['Year_return_excess_kurtosis'][i] = year_returns['Return_{0}'.format(company_names[i])].kurtosis()-3
        tabla['Year_best'][i] = year_returns['Return_{0}'.format(company_names[i])].max()
        tabla['Year_worst'][i] = year_returns['Return_{0}'.format(company_names[i])].min()
        tabla['Year_max_drawdawn'][i] = year_returns['Drawdawn_{0}'.format(company_names[i])].min()
        tabla['Year_historical_VaR'][i] = year_returns['Return_{0}'.format(company_names[i])].quantile(0.05)
        tabla['Year_gaussian_VaR'][i] = tabla['Year_return_mean_arithmetic'][i] + norm.ppf(0.05)*tabla['Year_return_stdev'][i]
        z = norm.ppf(0.05)
        s = tabla['Year_return_skewness'][i]
        k = tabla['Year_return_excess_kurtosis'][i]+3
        z = (z + (z**2 - 1)*s/6 + (z**3 -3*z)*(k-3)/24 -(2*z**3 - 5*z)*(s**2)/36)
        tabla['Year_cornish-fisher_VaR'][i] = tabla['Year_return_mean_arithmetic'][i] + z*tabla['Year_return_stdev'][i]
        tabla['Year_CVaR'][i] = year_returns['Return_{0}'.format(company_names[i])].where(year_returns['Return_{0}'.format(company_names[i])] < tabla['Year_cornish-fisher_VaR'][i]).mean()
        tabla['Sharpe_ratio'][i] = tabla['Year_return_mean_geometric'][i]/tabla['Year_return_stdev'][i]
        tabla['Sortino_ratio'][i] = tabla['Year_return_mean_geometric'][i]/tabla['Year_return_stdev_downside'][i]
        tabla['Beta'][i] = stats.linregress(day_returns['Benchmark_return_sp500'].values,day_returns['Return_{0}'.format(company_names[i])].values)[0]
        tabla['Alpha'][i] = stats.linregress(year_returns['Benchmark_return_sp500'].values,year_returns['Return_{0}'.format(company_names[i])].values)[1]
        tabla['Treynor_ratio'][i] = tabla['Year_return_mean_geometric'][i]/tabla['Beta'][i]
        #tabla['Calmar_ratio'][i] = tabla['Year_return_mean_geometric'][i]/abs(tabla['Year_max_drawdawn'][i])
        sp500_geometric_month_return = month_returns['Benchmark_return_sp500'].add(1).prod()**(1/month_returns.shape[0])-1
        sp500_geometric_annual_return = (1+sp500_geometric_month_return)**12-1
        tabla['Active_return'][i] = tabla['Year_return_mean_geometric'][i] - sp500_geometric_annual_return
        tabla['Tracking_error'][i] = (year_returns['Return_{0}'.format(company_names[i])]-year_returns['Benchmark_return_sp500']).std()
        tabla['Information_ratio'][i] = tabla['Active_return'][i]/tabla['Tracking_error'][i]
        tabla['%Day_up'][i] = day_returns[day_returns['Return_{0}'.format(company_names[i])]>0].shape[0]*100/day_returns.shape[0]
        tabla['%Week_up'][i] = week_returns[week_returns['Return_{0}'.format(company_names[i])]>0].shape[0]*100/week_returns.shape[0]
        tabla['%Month_up'][i] = month_returns[month_returns['Return_{0}'.format(company_names[i])]>0].shape[0]*100/month_returns.shape[0]
        tabla['%Year_up'][i] = year_returns[year_returns['Return_{0}'.format(company_names[i])]>0].shape[0]*100/year_returns.shape[0]
        
    return tabla

In [4]:
%%time
financial_data_quarter_all = load_obj("financial_data_quarter")
financial_data_quarter_all = financial_data_quarter_all.replace(' ', '_', regex=True)

financial_data_year_all = load_obj("financial_data_year")
financial_data_year_all = financial_data_year_all.replace(' ', '_', regex=True)

Wall time: 28.1 s


# Parameters 

In [28]:
#Parameters(asegurarse de que son días entre semana)
start_date = '1980-01-02' #Formato año-mes-dia: 3 de enero de 2013 #print(calendar.weekday(2013, 1, 2)) #Formato año,mes,dia
final_date = '2020-06-26' #Formato año-mes-dia: 3 de enero de 2020 #print(calendar.weekday(2020, 1, 31))
#company_tickers = ["VRSK","INFO","MSCI","SPGI","MCO"]
#company_tickers = ["VRSK","INFO","MSCI","SPGI","MCO"]
#company_tickers = ['MSFT','FB','NFLX','ADBE','PYPL','NOW','SQ','AYX','TTD','WIX'] 'CRM',"ROKU",'PAYC','VEEV',
company_tickers = ['ADBE','PYPL','NFLX','CRM','NOW']
initial_investment = 10000
company_weighs = [1/len(company_tickers)]*len(company_tickers)
benchmark_tickers = ['^GSPC','^IXIC']
benchmark_names = ['sp500','nasdaq']

###############Company names##################
for company in company_tickers:
    company_names.append(financial_data_year_all[financial_data_year_all['Ticker Symbol']==company]['Company'].values[0])
company_names.append('total')
print(company_names)

financial_data_year = financial_data_year_all[financial_data_year_all['Ticker Symbol'].isin(company_tickers)]
#financial_data_year.sort_values(by="Calendar Date").head(10)

# #Day prices # amzn = load_obj(company_tickers[0])# facebook = load_obj(company_tickers[1])# netflix = load_obj(company_tickers[2])

# #Benchmark # sp500 = load_obj(benchmark_tickers[0])# nasdaq = load_obj(benchmark_tickers[1])

# #Week prices# amzn_week = week_prices(amzn)# facebook_week = week_prices(facebook)# netflix_week = week_prices(netflix)# sp500_week = week_prices(sp500)#nasdaq_week = week_prices(nasdaq)

# #Month prices# amzn_month = month_prices(amzn)# facebook_month = month_prices(facebook)# netflix_month = month_prices(netflix)# sp500_month = month_prices(sp500)# nasdaq_month = month_prices(nasdaq)

# #Year prices# amzn_year = year_prices(amzn,start_date,final_date)# facebook_year = year_prices(facebook,start_date,final_date)# netflix_year = year_prices(netflix,start_date,final_date)# sp500_year = year_prices(sp500,start_date,final_date)# nasdaq_year = year_prices(nasdaq,start_date,final_date)

['SQ', 'AYX', 'TTD', 'ROKU', 'WIX', 'PAYC', 'VEEV', 'Verisk_Analytics_Inc', 'IHS_Markit_Ltd', 'MSCI_Inc', 'S&P_Global_Inc', 'Moodys_Corp', 'total', 'Square_Inc', 'Alteryx_Inc', 'Trade_Desk_Inc', 'Roku_Inc', 'Wixcom_Ltd', 'Paycom_Software_Inc', 'Veeva_Systems_Inc', 'total', 'Adobe_Inc', 'PayPal_Holdings_Inc', 'Netflix_Inc', 'Salesforcecom_Inc', 'ServiceNow_Inc', 'total']


In [29]:
#Market cap
financial_data_year['Factor of variation in market cap'] = financial_data_year.groupby('Ticker Symbol')['Market Capitalization - Daily'].apply(lambda x: 1+x.div(x.iloc[0]).subtract(1))
financial_data_year['%Year change in market cap'] = financial_data_year.groupby('Ticker Symbol')['Market Capitalization - Daily'].pct_change()*100

#Revenues
financial_data_year['Factor of variation in revenues'] = financial_data_year.groupby('Ticker Symbol')['Revenues'].apply(lambda x: 1+x.div(x.iloc[0]).subtract(1))
financial_data_year['%Year change in revenues'] = financial_data_year.groupby('Ticker Symbol')['Revenues'].pct_change()*100

#Net income
financial_data_year['Factor of variation in net income'] = financial_data_year.groupby('Ticker Symbol')['Net Income'].apply(lambda x: 1+x.div(x.iloc[0]).subtract(1))
financial_data_year['%Year change in net income'] = financial_data_year.groupby('Ticker Symbol')['Net Income'].pct_change()*100

############################################Expenses####################################################
#Percent expense in capex
financial_data_year['Capex/revenues'] = financial_data_year['Capital Expenditure']*100/financial_data_year['Revenues']

#Percent expense in research and development
financial_data_year['R&D/revenues'] = financial_data_year['Research and Development Expense']*100/financial_data_year['Revenues']

#Percent expense in selling, general & administrative
financial_data_year['SG&A/revenues'] = financial_data_year['Selling General and Administrative Expense']*100/financial_data_year['Revenues']

#Interest expense
financial_data_year['Interest expese/revenues'] = financial_data_year['Interest Expense']*100/financial_data_year['Revenues']

#Share based compensation
financial_data_year['Share Based Compensation/revenues'] = financial_data_year['Share Based Compensation']*100/financial_data_year['Revenues']

##########################################Debt ratios########################################################



#########################################Profitability ratios################################################
financial_data_year['PS/Rev_growth'] = financial_data_year['Price to Sales Ratio']/(financial_data_year['%Year change in revenues']+1)

# Financial results

##### Individual plots

In [30]:
%%time
order_list = financial_data_year.sort_values(by="Company",ascending=True)['Company'].unique().tolist()
category_orders={'Company': order_list}

#####################################Market cap, price and number of shares###################################
#Market cap
market_cap = px.line(financial_data_year, x="Calendar Date", y="Market Capitalization - Daily", #barmode='group',
                     #facet_col = "Company",
                     color="Company",title="Market cap", category_orders = category_orders)
    
#Number of shares
shares = px.line(financial_data_year, x="Calendar Date", y="Shares (Basic)", 
                facet_col = "Company",
                color="Company",title="Shares", category_orders = category_orders)

#Price
price_per_share = px.line(financial_data_year, x="Calendar Date", y="Price", 
                facet_col = "Company",
                color="Company",title="Shares", category_orders = category_orders)


##########################################P&L values################################################
#Revenues
revenues = px.bar(financial_data_year, x="Calendar Date", y="Revenues", #barmode='group',
                  #facet_col = "Company",
                  color="Company",title="Revenues", category_orders = category_orders)

#Net income
net_income = px.bar(financial_data_year, x="Calendar Date", y="Net Income", 
       facet_col = "Company",color="Company",title="Net income", category_orders = category_orders)

###########################################Valuation ratios################################################
#Price to sales
price_to_sales = px.bar(financial_data_year, x="Calendar Date", y="Price to Sales Ratio", 
                        #facet_col = "Company",
                        color="Company",title="P/S", category_orders = category_orders)

#Price to earnings
price_to_earnings = px.bar(financial_data_year,x="Calendar Date",y="Price to Earnings Ratio",
                          color="Company",title="P/E",category_orders = category_orders)

ps_to_revenue_growth = px.line(financial_data_year,x="Calendar Date",y="PS/Rev_growth",
                          color="Company",title="PS to revenue growth",category_orders = category_orders)


#########################################Growth measures###############################################
market_cap_change = px.bar(financial_data_year, x="Calendar Date", y='%Year change in market cap', #barmode='group',
                  #facet_col = "Company",
                  color="Company",title='%Year change in market cap', category_orders = category_orders)


revenue_change = px.bar(financial_data_year, x="Calendar Date", y='%Year change in revenues', #barmode='group',
                  #facet_col = "Company",
                  color="Company",title='%Year change in revenues', category_orders = category_orders)

net_income_change = px.bar(financial_data_year, x="Calendar Date", y='%Year change in net income', #barmode='group',
                  #facet_col = "Company",
                  color="Company",title='%Year change in net income', category_orders = category_orders)

#########################################Factor growth measures###############################################
market_cap_factor = px.bar(financial_data_year, x="Calendar Date", y='Factor of variation in market cap', #barmode='group',
                  #facet_col = "Company",
                  color="Company",title='%Year change in market cap', category_orders = category_orders)


revenue_factor = px.bar(financial_data_year, x="Calendar Date", y='Factor of variation in revenues', #barmode='group',
                  #facet_col = "Company",
                  color="Company",title='%Year change in revenues', category_orders = category_orders)

net_income_factor = px.bar(financial_data_year, x="Calendar Date", y='Factor of variation in net income', #barmode='group',
                  #facet_col = "Company",
                  color="Company",title='%Year change in net income', category_orders = category_orders)

#####################################Operating margins######################################################
gross_margin = px.line(financial_data_year, x="Calendar Date",y="Gross Margin",
                      color="Company",title="Gross margin",category_orders=category_orders)

ebitda_margin = px.line(financial_data_year,x="Calendar Date", y ="EBITDA Margin",
                       color="Company",title="EBITDA margin",category_orders=category_orders)

net_margin = px.line(financial_data_year,x="Calendar Date",y="Profit Margin",
                    color="Company",title="Net margin",category_orders=category_orders)


################################Expenditures############################################################
capex = px.line(financial_data_year)


#double_axis(revenues,market_cap,title="a",x_label="b",left_y_label="c",right_y_label="d",number_of_traces=len(order_list))

Wall time: 6.92 s


###### Make subplots

In [31]:
############Market cap, price and number of shares#################
fig_1 = make_subplots(rows=1, cols=3,subplot_titles=("Market cap","Number of shares","Price"))

for i in range (0,len(company_tickers)):
    fig_1.add_trace(market_cap.data[i], row=1, col=1)
    fig_1.add_trace(shares.data[i], row=1, col=2)
    fig_1.add_trace(price_per_share.data[i], row=1, col=3)

fig_1.update_layout(title_text="Market cap, number of shares and price of stocks")
fig_1.show()


############Revenues#################
fig_revenues = make_subplots(rows=1, cols=5,subplot_titles=("Market cap","Revenue","Price to sales","Revenue growth","PS to Revenue growth"))

for i in range (0,len(company_tickers)):
    fig_revenues.add_trace(market_cap.data[i], row=1, col=1)
    fig_revenues.add_trace(revenues.data[i], row=1, col=2)
    fig_revenues.add_trace(price_to_sales.data[i], row=1, col=3)
    fig_revenues.add_trace(revenue_change.data[i], row=1, col=4)
    fig_revenues.add_trace(ps_to_revenue_growth.data[i], row=1, col=5)

fig_revenues.update_layout(title_text="Revenue metrics")

fig_revenues.show()

#########Net income####################
fig_net_income = make_subplots(rows=1, cols=4,subplot_titles=("Market cap", "Net income","Price to earnings","Net income growth"))

for i in range (0,len(company_tickers)):
    fig_net_income.add_trace(market_cap.data[i], row=1, col=1)
    fig_net_income.add_trace(net_income.data[i], row=1, col=2)
    fig_net_income.add_trace(price_to_earnings.data[i], row=1, col=3)
    fig_net_income.add_trace(net_income_change.data[i], row=1, col=4)

fig_net_income.update_layout(title_text="Net income metrics")
fig_net_income.show()

#Margins
fig_margin = make_subplots(rows=1, cols=3, subplot_titles=("Gross margin", "EBITDA margin","Net margin"))

for i in range (0,len(company_tickers)):
    fig_margin.add_trace(gross_margin.data[i], row=1, col=1)
    fig_margin.add_trace(ebitda_margin.data[i], row=1, col=2)
    fig_margin.add_trace(net_margin.data[i], row=1, col=3)

fig_margin.update_layout(title_text="Margins")
fig_margin.show()

In [23]:
if (financial_data_year['Is Delisted?'] == "Y").any():
    print("Yes")
    s = '_'
    fecha = str(datetime.datetime.now().strftime("%Y-%m-%d__%H-%M-%S_"))
    var = str(fecha + "_" + s.join(company_names)+ '.html')
    var = var.replace("/","_")

    !jupyter nbconvert 2.Portfolio_performance_optimized.ipynb --no-input --output-dir='./html_sin_codigo' --to html --output output.html
    !jupyter nbconvert 2.Portfolio_performance_optimized.ipynb --output-dir='./html_con_codigo' --to html --output output.html

    os.rename('./html_sin_codigo/output.html', './html_sin_codigo/' + var)
    os.rename('./html_con_codigo/output.html','./html_con_codigo/'+ var)
    raise SystemExit("Stop right there!")

# Price results

## Tablas

In [10]:
#Portfolio companies
company_list = []
for i in range (0,len(company_tickers)):
    company_list.append(download_data([company_tickers[i]]))
    
company_list_week = []
for i in range (0,len(company_tickers)):
    company_list_week.append(week_prices(download_data([company_tickers[i]])))

company_list_month = []
for i in range (0,len(company_tickers)):
    company_list_month.append(month_prices(download_data([company_tickers[i]])))

company_list_year = []
for i in range (0,len(company_tickers)):
    company_list_year.append(year_prices(download_data([company_tickers[i]]),start_date,final_date))
    
#Benchmark
benchmark = []
for i in range(0,len(benchmark_tickers)):
    benchmark.append(download_data([benchmark_tickers[i]]))

benchmark_month = []
for i in range(0,len(benchmark_tickers)):
    benchmark_month.append(month_prices(download_data([benchmark_tickers[i]])))
    
benchmark_year = []
for i in range(0,len(benchmark_tickers)):
    benchmark_year.append(year_prices(download_data([benchmark_tickers[i]]),start_date,final_date))

In [11]:
print(company_names)

['Verisk_Analytics_Inc', 'IHS_Markit_Ltd', 'MSCI_Inc', 'S&P_Global_Inc', 'Moodys_Corp', 'total']


In [12]:
%%time
#Day returns and day wealth index
day_returns = portfolio_return(company_list,company_names,company_weighs, initial_investment,
                               start_date,final_date,benchmark,benchmark_names)
display(day_returns.head())
#display(day_returns.shape[0])

#Week returns and week wealth index
week_returns = portfolio_return(company_list_week,company_names,company_weighs, initial_investment,
                               start_date,final_date,benchmark,benchmark_names)

#Month returns and month wealth index
month_returns = portfolio_return(company_list_month,company_names,company_weighs, initial_investment,
                                 start_date,final_date,benchmark_month,benchmark_names)
#display(month_returns.tail(30))
#display(month_returns.shape[0])

#Year returns and year wealth index
year_returns = portfolio_return(company_list_year,company_names,company_weighs, initial_investment,
                                start_date,final_date,benchmark_year,benchmark_names)
#display(year_returns.head(10))
#display(year_returns.shape[0])

#Information table
my_table = tabla(day_returns,week_returns,month_returns,year_returns,company_names)
my_table

sp500
nasdaq


Year  Day Day_of_week       Date  Price_Verisk_Analytics_Inc  \
0  2014  171     Viernes 2014-06-20                       59.83   
1  2014  174       Lunes 2014-06-23                       59.74   
2  2014  175      Martes 2014-06-24                       58.92   
3  2014  176   Miercoles 2014-06-25                       58.62   
4  2014  177      Jueves 2014-06-26                       58.54   

   Volume_Verisk_Analytics_Inc  Return_Verisk_Analytics_Inc  \
0                      1016800                     0.004196   
1                       719900                    -0.001504   
2                      1070900                    -0.013726   
3                       904200                    -0.005092   
4                       562900                    -0.001365   

   Investment_acumulado_Verisk_Analytics_Inc  Price_IHS_Markit_Ltd  \
0                                2000.000000                 26.83   
1                                2008.392078                 26.62   
2                                2005.370930                 26.64   
3                                1977.844914                 26.78   
4                                1967.774421                 26.82   

   Volume_IHS_Markit_Ltd  Return_IHS_Markit_Ltd  \
0                3840000               0.009406   
1                1526300              -0.007827   
2                1102900               0.000751   
3                 921100               0.005255   
4                1034900               0.001494   

   Investment_acumulado_IHS_Markit_Ltd  Price_MSCI_Inc  Volume_MSCI_Inc  \
0                          2000.000000           41.56          1192600   
1                          2018.811136           41.82           475100   
2                          2003.009782           41.43           575600   
3                          2004.514673           41.57           345900   
4                          2015.048909           41.45           319600   

   Return_MSCI_Inc  Investment_acumulado_MSCI_Inc  Price_S&P_Global_Inc  \
0        -0.007641                    2000.000000                 77.15   
1         0.006256                    1984.718243                 77.40   
2        -0.009326                    1997.134670                 77.37   
3         0.003379                    1978.510029                 77.01   
4        -0.002887                    1985.195798                 77.15   

   Volume_S&P_Global_Inc  Return_S&P_Global_Inc  \
0                1541800              -0.001036   
1                 811400               0.003240   
2                1465800              -0.000388   
3                 829500              -0.004653   
4                 620100               0.001818   

   Investment_acumulado_S&P_Global_Inc  Price_Moodys_Corp  Volume_Moodys_Corp  \
0                          2000.000000              80.15              879800   
1                          1997.928266              80.65              607300   
2                          2004.402434              80.62              705800   
3                          2003.625534              80.44             1191300   
4                          1994.302732              80.66              641000   

   Return_Moodys_Corp  Investment_acumulado_Moodys_Corp  \
0            0.008557                       2000.000000   
1            0.006238                       2017.113376   
2           -0.000372                       2029.696741   
3           -0.002233                       2028.941739   
4            0.002735                       2024.411728   

   Investment_acumulado_total  Percentage_allocation_Verisk_Analytics_Inc  \
0                10000.000000                                    0.200000   
1                10026.963099                                    0.200299   
2                10039.614557                                    0.199746   
3                 9993.436889                                    0.197914   
4                 9986.733587                            

sp500
nasdaq
sp500
nasdaq
sp500
nasdaq
Wall time: 2.64 s


Stock  Day_return_mean_arithmetic  \
0  Verisk_Analytics_Inc                    0.000765   
1        IHS_Markit_Ltd                    0.000794   
2              MSCI_Inc                    0.001531   
3        S&P_Global_Inc                    0.001082   
4           Moodys_Corp                    0.000962   
5                 total                    0.001049   

   Day_return_mean_geometric  Day_return_stdev  Day_return_stdev_downside  \
0                   0.000664          0.014201                   0.011874   
1                   0.000664          0.016348                   0.011535   
2                   0.001367          0.018155                   0.013544   
3                   0.000941          0.016754                   0.013389   
4                   0.000805          0.017722                   0.014732   
5                   0.000945          0.014428                   0.011755   

   Day_return_skewness  Day_return_excess_kurtosis  Day_best  Day_worst  \
0            -0.040705                   13.338795  0.132832  -0.106831   
1             3.281874                   65.496992  0.283948  -0.124657   
2             0.391599                   10.602399  0.180370  -0.130573   
3            -0.126646                   11.506600  0.138541  -0.151869   
4             0.004051                   14.180342  0.185759  -0.137268   
5             0.525644                   22.683456  0.179453  -0.116673   

   Day_max_drawdawn  Day_historical_VaR  Day_gaussian_VaR  \
0         -0.292390           -0.019298         -0.022594   
1         -0.440242           -0.019193         -0.026097   
2         -0.322197           -0.023878         -0.028331   
3         -0.381367           -0.021240         -0.026476   
4         -0.420189           -0.024296         -0.028189   
5         -0.353851           -0.020379         -0.022683   

   Day_cornish-fisher_VaR  Day_CVaR  Month_return_mean_arithmetic  \
0               -0.018935 -0.032854                      0.016070   
1                0.014070 -0.002251                      0.015454   
2               -0.022373 -0.037397                      0.031909   
3               -0.023184 -0.040910                      0.022559   
4               -0.023097 -0.040798                      0.019657   
5               -0.013847 -0.026100                      0.021721   

   Month_return_mean_geometric  Month_return_stdev  \
0                     0.014636            0.053661   
1                     0.013694            0.059837   
2                     0.029222            0.074493   
3                     0.020374            0.066977   
4                     0.017035            0.072476   
5                     0.020188            0.055690   

   Month_return_stdev_downside  Month_return_skewness  \
0                     0.038522              -0.638415   
1                     0.044053              -0.010773   
2                     0.049172              -0.120575   
3                     0.041996              -0.060204   
4                     0.051397              -0.457794   
5                     0.043012              -0.505363   

   Month_return_excess_kurtosis  Month_best  Month_worst  Month_max_drawdawn  \
0                     -2.645810    0.107944    -0.135449           -0.146371   
1                      1.701757    0.248754    -0.206685           -0.266616   
2                     -2.307589    0.226077    -0.180792           -0.191705   
3                     -1.798051    0.220759    -0.190031           -0.205633   
4                     -1.266345    0.224229    -0.238801           -0.241584   
5                     -1.093043    0.173041    -0.174061           -0.174061   

   Month_historical_VaR  Month_gaussian_VaR  Month_cornish-fisher_VaR  \
0             -0.075468           -0.072195                 -0.084388   
1             -0.066832           -0.082970                 -0.081098   
2             -0.082336           -0.090620                 -0.096622   
3             -0.08157

## Wealth index plot & drawdawn

In [13]:
#Wealth index plot
df1 = day_returns.loc[:, day_returns.columns.str.contains('Date|Inv')]
df1 = df1.melt(id_vars=["Date"], var_name="Company", value_name="Investment_acumulado").sort_values(by="Date")
display(df1.head())
order_list1 = df1.sort_values(by="Company",ascending=True)['Company'].unique().tolist()
order_list1.remove('Investment_acumulado_total')
order_list1.append("Investment_acumulado_total")

df2 = day_returns.loc[:, day_returns.columns.str.contains('Date|inv')]
df2 = df2.melt(id_vars=["Date"], var_name="Company", value_name="Investment_acumulado").sort_values(by="Date")
order_list2 = df2.sort_values(by="Company",ascending=True)['Company'].unique().tolist()

##########################Concatenamos####################################
df = pd.concat([df1,df2]).sort_values(by="Date")
category_orders={'Company': order_list1 + order_list2}

#Plot
annual_returns = px.line(df, x="Date", y="Investment_acumulado", #log_y=True,
                         color="Company",title="Return on investment",category_orders = category_orders)

annual_returns.update_layout(title_text="Investment acumulado over time",
                          updatemenus=[dict(buttons=[
                                                     dict(label="Linear",  method="relayout",args=[{"yaxis.type": "linear"}]),
                                                     dict(label="Log", method="relayout", args=[{"yaxis.type": "log"}]) ])])
            
annual_returns.update_xaxes(
    #rangeslider_visible=True,
    rangeselector=dict(
        buttons=list([
            dict(count=1, label="1m", step="month", stepmode="backward"),
            dict(count=6, label="6m", step="month", stepmode="backward"),
            dict(count=1, label="YTD", step="year", stepmode="todate"),
            dict(count=1, label="1y", step="year", stepmode="backward"),
            dict(step="all")
        ])
    ))
annual_returns.show()
###############################################################################################################################
#########################Drawdawns##################################
df1 = day_returns.loc[:, day_returns.columns.str.contains('Date|Drawdawn')]
df1 = df1.melt(id_vars=["Date"], var_name="Company", value_name="Drawdawn").sort_values(by="Date")
order_list1 = df1.sort_values(by="Company",ascending=True)['Company'].unique().tolist()
order_list1.remove('Drawdawn_total')
order_list1.append("Drawdawn_total")

df2 = day_returns.loc[:, day_returns.columns.str.contains('Date|drawdawn')]
df2 = df2.melt(id_vars=["Date"], var_name="Company", value_name="Drawdawn").sort_values(by="Date")
order_list2 = df2.sort_values(by="Company",ascending=True)['Company'].unique().tolist()

##########################Concatenamos####################################
df = pd.concat([df1,df2]).sort_values(by="Date")
category_orders={'Company': order_list1 + order_list2}

#Plot
drawdawns = px.area(df, x="Date", y="Drawdawn",color="Company",
                    facet_col="Company",facet_col_wrap=2,
                    category_orders = category_orders,
                    title="Drawdawn")
drawdawns.show()

Date                                    Company  \
0    2014-06-20  Investment_acumulado_Verisk_Analytics_Inc   
6064 2014-06-20           Investment_acumulado_Moodys_Corp   
4548 2014-06-20        Investment_acumulado_S&P_Global_Inc   
3032 2014-06-20              Investment_acumulado_MSCI_Inc   
1516 2014-06-20        Investment_acumulado_IHS_Markit_Ltd   

      Investment_acumulado  
0                   2000.0  
6064                2000.0  
4548                2000.0  
3032                2000.0  
1516                2000.0

## Price plot & volume plot

In [14]:
###############################################################################################################################
###########################Price plot###########################
# df1 = day_returns.loc[:, day_returns.columns.str.contains('Date|Price')]
# df1 = df1.melt(id_vars=["Date"], var_name="Company", value_name="Price").sort_values(by="Date")
# order_list1 = df1.sort_values(by="Company",ascending=True)['Company'].unique().tolist()

# df2 = day_returns.loc[:, day_returns.columns.str.contains('Date|price')]
# df2 = df2.melt(id_vars=["Date"], var_name="Company", value_name="Price").sort_values(by="Date")
# order_list2 = df2.sort_values(by="Company",ascending=True)['Company'].unique().tolist()

# ##########################Concatenamos####################################
# df = pd.concat([df1,df2]).sort_values(by="Date")
# category_orders={'Company': order_list1 + order_list2}

# price = px.line(df, x="Date", y="Price", #log_y=True,
#                          color="Company",title="Stock volume",category_orders = category_orders)

# price.update_layout(title_text="Price over time",
#                           updatemenus=[dict(buttons=[
#                                                      dict(label="Linear",  method="relayout",args=[{"yaxis.type": "linear"}]),
#                                                      dict(label="Log", method="relayout", args=[{"yaxis.type": "log"}]) ])])
# price.show()
# ###############################################################################################################################
# ###########################Volume plot###########################
# df1 = day_returns.loc[:, day_returns.columns.str.contains('Date|Volume')]
# df1 = df1.melt(id_vars=["Date"], var_name="Company", value_name="Volume").sort_values(by="Date")
# order_list1 = df1.sort_values(by="Company",ascending=True)['Company'].unique().tolist()

# df2 = day_returns.loc[:, day_returns.columns.str.contains('Date|volume')]
# df2 = df2.melt(id_vars=["Date"], var_name="Company", value_name="Volume").sort_values(by="Date")
# order_list2 = df2.sort_values(by="Company",ascending=True)['Company'].unique().tolist()

# ##########################Concatenamos####################################
# df = pd.concat([df1,df2]).sort_values(by="Date")
# category_orders={'Company': order_list1 + order_list2}

# volume = px.line(df, x="Date", y="Volume", #log_y=True,
#                          color="Company",title="Stock volume",category_orders = category_orders)

# volume.update_layout(title_text="Volume over time",
#                           updatemenus=[dict(buttons=[
#                                                      dict(label="Linear",  method="relayout",args=[{"yaxis.type": "linear"}]),
#                                                      dict(label="Log", method="relayout", args=[{"yaxis.type": "log"}]) ])])
volume.show()

## Returns over time with VaR and CVaR

In [15]:
################################Allocation over time##################################
#Stacked barplot relative
df = year_returns.loc[:, year_returns.columns.str.contains('Year|allocation')]
display(df.head())
df = df.melt(id_vars=["Year"], 
        var_name="Company", 
        value_name="Allocation").sort_values(by="Year")

#Ordenamos las categorías
order_list = df.sort_values(by="Company",ascending=True)['Company'].unique().tolist()
category_orders={'Company': order_list}

allocation_drift = px.area(df, x="Year", y="Allocation", color="Company",
                           title="Allocation drift",category_orders = category_orders)
allocation_drift.show()

#################################Day level##########################################################

##################################Day returns over time per company##############################################
df = day_returns.loc[:, day_returns.columns.str.contains('Date|Return')]
df = df.loc[:, ~df.columns.str.contains('total')]
df = df.melt(id_vars=["Date"], var_name="Company", value_name="Return").sort_values(by="Date")
order_list = df.sort_values(by="Company",ascending=True)['Company'].unique().tolist()
category_orders={'Company': order_list}

#Plots
returns_fluctuations_day = px.line(df, x="Date", y="Return",
                                   color="Company",
                                   facet_col ="Company",
                                   category_orders = category_orders,
                                   title="Day returns over time (by company)")
returns_fluctuations_day.data[-1].showlegend = True
returns_fluctuations_day.show()

##################################Day returs over time of the total portfolio########################
df = day_returns[['Date','Return_total']]
df = df.melt(id_vars=["Date"], var_name="Legend", value_name="Return").sort_values(by="Date")

#Plots
returns_fluctuations_day = px.line(df, x="Date", y="Return",
                                    title="Day returns over time (total portfolio)",
                                    color_discrete_sequence = ["blue"])
returns_fluctuations_day.data[-1].name = 'Returns per month'
returns_fluctuations_day.data[-1].showlegend = True

df['Day_historical_VaR'] = my_table[my_table.Stock=='total']['Day_historical_VaR'].item()
df['Day_gaussian_VaR'] = my_table[my_table.Stock=='total']['Day_gaussian_VaR'].item()
df['Day_cornish-fisher_VaR'] = my_table[my_table.Stock=='total']['Day_cornish-fisher_VaR'].item()
df['Day_CVaR'] = my_table[my_table.Stock=='total']['Day_CVaR'].item()

historical_var = px.line(df, x="Date", y="Day_historical_VaR",line_dash_sequence=['dash'],
                          title="Histogram of day returns",color_discrete_sequence = ["green"])
historical_var.data[-1].name = 'Historical VaR'
historical_var.data[-1].showlegend = True

cornish_fisher_var = px.line(df, x="Date", y="Day_cornish-fisher_VaR",line_dash_sequence=['dash'],
                          title="Histogram of day returns",color_discrete_sequence = ["orange"])
cornish_fisher_var.data[-1].name = 'Cornish-Fisher VaR'
cornish_fisher_var.data[-1].showlegend = True

cvar = px.line(df, x="Date", y="Day_CVaR",line_dash_sequence=['dash'],
                          title="Histogram of day returns",color_discrete_sequence = ["red"])
cvar.data[-1].name = 'CVaR'
cvar.data[-1].showlegend = True

returns_fluctuations_day.add_trace(historical_var.data[0]).add_trace(cornish_fisher_var.data[0]).add_trace(cvar.data[0]).show()
print("Numero de trading days:",df.shape[0])


#################################Month level##########################################################

##################################Month returns over time per company##############################################
df = month_returns.loc[:, month_returns.columns.str.contains('Date|Return')]
df = df.loc[:, ~df.columns.str.contains('total')]
df = df.melt(id_vars=["Date"], var_name="Company", value_name="Return").sort_values(by="Date")
order_list = df.sort_values(by="Company",ascending=True)['Company'].unique().tolist()
category_orders={'Company': order_list}

#Plots
returns_fluctuations_month = px.line(df, x="Date", y="Return",
                                   color="Company",
                                   facet_col ="Company",
                                   category_orders = category_orders,
                                   title="Month returns over time (by company)")
returns_fluctuations_month.data[-1].showlegend = True
returns_fluctuations_month.show()

####################################################Month returns over time##############################################
df = month_returns[['Date','Return_total']]
df = df.melt(id_vars=["Date"], var_name="Legend", value_name="Return").sort_values(by="Date")

#Plots
returns_fluctuations_month = px.bar(df, x="Date", y="Return",
                                    title="Month returns over time (total portfolio)",
                                    color_discrete_sequence = ["blue"])
returns_fluctuations_month.data[-1].name = 'Returns per month'
returns_fluctuations_month.data[-1].showlegend = True

df['Month_historical_VaR'] = my_table[my_table.Stock=='total']['Month_historical_VaR'].item()
df['Month_gaussian_VaR'] = my_table[my_table.Stock=='total']['Month_gaussian_VaR'].item()
df['Month_cornish-fisher_VaR'] = my_table[my_table.Stock=='total']['Month_cornish-fisher_VaR'].item()
df['Month_CVaR'] = my_table[my_table.Stock=='total']['Month_CVaR'].item()


historical_var = px.line(df, x="Date", y="Month_historical_VaR",line_dash_sequence=['dash'],
                          title="Histogram of month returns",color_discrete_sequence = ["green"])
historical_var.data[-1].name = 'Historical VaR'
historical_var.data[-1].showlegend = True

cornish_fisher_var = px.line(df, x="Date", y="Month_cornish-fisher_VaR",line_dash_sequence=['dash'],
                          title="Histogram of month returns",color_discrete_sequence = ["orange"])
cornish_fisher_var.data[-1].name = 'Cornish-Fisher VaR'
cornish_fisher_var.data[-1].showlegend = True

cvar = px.line(df, x="Date", y="Month_CVaR",line_dash_sequence=['dash'],
                          title="Month returns over time",color_discrete_sequence = ["red"])
cvar.data[-1].name = 'CVaR'
cvar.data[-1].showlegend = True

returns_fluctuations_month.add_trace(historical_var.data[0]).add_trace(cornish_fisher_var.data[0]).add_trace(cvar.data[0]).show()
print("Numero de trading months:",df.shape[0])


#################################Year level##########################################################

##################################Year returns over time per company##############################################
df = year_returns.loc[:, year_returns.columns.str.contains('Date|Return')]
df = df.loc[:, ~df.columns.str.contains('total')]
df = df.melt(id_vars=["Date"], var_name="Company", value_name="Return").sort_values(by="Date")
order_list = df.sort_values(by="Company",ascending=True)['Company'].unique().tolist()
category_orders={'Company': order_list}

#Plots
returns_fluctuations_year = px.bar(df, x="Date", y="Return",
                                   color="Company",
                                   facet_col ="Company",
                                   category_orders = category_orders,
                                   title="Year returns over time (by company)")
#returns_fluctuations_year.update_layout(bargroupgap=0.6)
#returns_fluctuations_year.update_layout(bargap=0.00001)
returns_fluctuations_year.data[-1].showlegend = True
returns_fluctuations_year.show()

####################################################Year returns over time##############################################
df = year_returns[['Date','Return_total']]
df = df.melt(id_vars=["Date"], var_name="Legend", value_name="Return").sort_values(by="Date")

#Plots
returns_fluctuations_year = px.bar(df, x="Date", y="Return",
                                    title="Year returns over time (total portfolio)",
                                    color_discrete_sequence = ["blue"])
returns_fluctuations_year.data[-1].name = 'Returns per year'
returns_fluctuations_year.data[-1].showlegend = True

df['Year_historical_VaR'] = my_table[my_table.Stock=='total']['Year_historical_VaR'].item()
df['Year_gaussian_VaR'] = my_table[my_table.Stock=='total']['Year_gaussian_VaR'].item()
df['Year_cornish-fisher_VaR'] = my_table[my_table.Stock=='total']['Year_cornish-fisher_VaR'].item()
df['Year_CVaR'] = my_table[my_table.Stock=='total']['Year_CVaR'].item()


historical_var = px.line(df, x="Date", y="Year_historical_VaR",line_dash_sequence=['dash'],
                          title="Histogram of year returns",color_discrete_sequence = ["green"])
historical_var.data[-1].name = 'Historical VaR'
historical_var.data[-1].showlegend = True

cornish_fisher_var = px.line(df, x="Date", y="Year_cornish-fisher_VaR",line_dash_sequence=['dash'],
                          title="Histogram of year returns",color_discrete_sequence = ["orange"])
cornish_fisher_var.data[-1].name = 'Cornish-Fisher VaR'
cornish_fisher_var.data[-1].showlegend = True

cvar = px.line(df, x="Date", y="Year_CVaR",line_dash_sequence=['dash'],
                          title="Year returns over time",color_discrete_sequence = ["red"])
cvar.data[-1].name = 'CVaR'
cvar.data[-1].showlegend = True

returns_fluctuations_year.add_trace(historical_var.data[0]).add_trace(cornish_fisher_var.data[0]).add_trace(cvar.data[0]).show()
print("Numero de trading years:",df.shape[0])

Year  Percentage_allocation_Verisk_Analytics_Inc  \
0  2015                                    0.200000   
1  2016                                    0.197875   
2  2017                                    0.193045   
3  2018                                    0.156687   
4  2019                                    0.164725   

   Percentage_allocation_IHS_Markit_Ltd  Percentage_allocation_MSCI_Inc  \
0                              0.200000                        0.200000   
1                              0.188181                        0.253952   
2                              0.204099                        0.259554   
3                              0.178565                        0.289676   
4                              0.175619                        0.316252   

   Percentage_allocation_S&P_Global_Inc  Percentage_allocation_Moodys_Corp  
0                              0.200000                           0.200000  
1                              0.185067                           0.174925  
2                              0.189039                           0.154262  
3                              0.206667                           0.168404  
4                              0.193924                           0.149479

Numero de trading days: 1516


Numero de trading months: 71


Numero de trading years: 517


## Seasonality and statistical measures

In [16]:
# ##################################Seasonality#############################
# #Heat map(corrplot)
# reduced = month_returns.pivot(index='Year', columns='Month', values='Return_total')
# reduced.iplot(kind='heatmap',colorscale="RdYLGn",title="Seasonality of returns")

# ###################################Histogram of day returns###############################
# df = day_returns.loc[:, day_returns.columns.str.contains('Date|Return')]
# df = df.melt(id_vars=["Date"], 
#         var_name="Company", 
#         value_name="Returns").sort_values(by="Date")

# #Ordenamos las categorías
# order_list = df.sort_values(by="Company",ascending=True)['Company'].unique().tolist()
# order_list.remove('Return_total')
# order_list.append("Return_total")
# category_orders={'Company': order_list}

# returns_histogram_day = px.histogram(df, x="Returns",color="Company",
#                           title="Histogram of day returns",barmode='overlay',category_orders=category_orders)
# returns_histogram_day.show()

# ###################################Histogram of month returns###############################
# df = month_returns.loc[:, month_returns.columns.str.contains('Date|Return')]
# df = df.melt(id_vars=["Date"], 
#         var_name="Company", 
#         value_name="Returns").sort_values(by="Date")

# #Ordenamos las categorías
# order_list = df.sort_values(by="Company",ascending=True)['Company'].unique().tolist()
# order_list.remove('Return_total')
# order_list.append("Return_total")
# category_orders={'Company': order_list}

# returns_histogram_month = px.histogram(df, x="Returns",color="Company",
#                           title="Histogram of month returns",barmode='overlay',category_orders=category_orders)
# returns_histogram_month.show()


# ###############################Comparison of day returns of total portfolio with normal distribution################
# df = day_returns['Return_total']
# real_returns = df.values

# #Simulation of normal distribution
# size = df.shape[0]
# mean = df.mean()
# stdev = df.std()
# np.random.seed(0) 
# normal_returns = np.random.normal(loc = mean, scale = stdev, size=size)

# ####################Plots#################################
# ##########Histogram#####
# #Histogram normal
# normal_histogram = px.histogram(pd.DataFrame(pd.Series(normal_returns)),x=0,
#                                 title="Histogram of normal day returns",color_discrete_sequence = ['red'],barmode='overlay')
# normal_histogram.data[-1].name = 'Simulated normal returns'
# normal_histogram.data[-1].showlegend = True

# #Histogram real
# real_histogram = px.histogram(pd.DataFrame(pd.Series(real_returns)),x=0,
#                               title="Histogram of real day returns",color_discrete_sequence = ['blue'],barmode='overlay')
# real_histogram.data[-1].name = 'Real returns'
# real_histogram.data[-1].showlegend = True

# #normal_histogram.add_trace(real_histogram.data[0]).show()

# #######Cumulative#######
# #Cumulative real
# df_real_cumulative = pd.DataFrame(df).sort_values(by="Return_total",ascending=True).\
#             reset_index().reset_index().drop(columns=['index']).rename(columns={"level_0":"cumulative","Return_total":"Real_returns"})
# df_real_cumulative['cumulative'] = df_real_cumulative['cumulative']+1
# df_real_cumulative['percentage'] = df_real_cumulative['cumulative']*100/df.shape[0]

# real_cumulative = px.line(df_real_cumulative,x='Real_returns',y='percentage',
#                                 title="Cumulative plot of real returns",color_discrete_sequence = ['blue'])
# real_cumulative.data[-1].name = 'Cumulative plot of real returns'
# real_cumulative.data[-1].showlegend = True

# #Cumulative normal
# df_normal_cumulative = pd.DataFrame(pd.Series(normal_returns)).sort_values(by=0,ascending=True).\
#                     reset_index().reset_index().drop(columns=['index']).rename(columns={0:"Normal_returns", "level_0":"cumulative"})
# df_normal_cumulative['cumulative'] = df_normal_cumulative['cumulative']+1
# df_normal_cumulative['percentage'] = df_normal_cumulative['cumulative']*100/df.shape[0]

# normal_cumulative = px.line(df_normal_cumulative,x='Normal_returns',y='percentage',
#                                 title="Cumulative plot of real returns",color_discrete_sequence = ['red'])
# normal_cumulative.data[-1].name = 'Cumulative plot of normal returns'
# normal_cumulative.data[-1].showlegend = True

# #real_cumulative.add_trace(normal_cumulative.data[0]).show()

# ####################### Double axis #####################################
# fig = make_subplots(specs=[[{"secondary_y": True}]])

# # Add traces
# fig.add_trace(real_histogram.data[0],secondary_y=False)
# fig.add_trace(normal_histogram.data[0],secondary_y=False)

# fig.add_trace(real_cumulative.data[0],secondary_y=True)
# fig.add_trace(normal_cumulative.data[0],secondary_y=True)

# # Add figure title
# fig.update_layout(title_text="Double Y Axis Example")

# # Set x-axis title
# fig.update_xaxes(title_text="xaxis title")

# # Set y-axes titles
# fig.update_yaxes(title_text="<b>Histogram plot</b> of returns", secondary_y=False)
# fig.update_yaxes(title_text="<b>Cumulative plot</b> of returns", secondary_y=True)

# fig.show()

# #####################################QQplots##########################
# #QQplot of normal returns
# stats.probplot(normal_returns,plot=pylab)
# pylab.title('QQ plot of normal distribution')
# pylab.show()

# #QQplot of real returns
# stats.probplot(real_returns,plot=pylab)
# pylab.title('QQ plot of real distribution')
# pylab.show()


# #####################################Statistical tests##########################
# #print("KS test de nuestra muestra real:", stats.kstest(real_returns,'norm',args=(mean, stdev)))
# p_value = stats.kstest(real_returns,'norm',args=(mean, stdev))[1]
# if p_value > 0.05:
#     print("La muestra de returns está normalizada: p_value=",p_value)
# else:
#     print("La muestra de returns no está normalizada: p_value=",p_value)

# print("-"*100)

# #Check if 2 distributions are equivalent
# np.random.seed(0) 
# normal_returns_1 = np.random.normal(loc = mean, scale = stdev, size=size)
# np.random.seed(1)
# normal_returns_2 = np.random.normal(loc = mean, scale = stdev, size=size)
# real_returns = df.values

# check = stats.ks_2samp(real_returns, real_returns)

# if check[1]>0.05:
#     print("pvalue>0.05, por lo tanto aceptamos la null hipotesis: las 2 distribuciones son equivalentes")
# else:
#     print("pvalue<0.05, por lo tanto rechazamos la null hipotesis: las 2 distribuciones son estadisticamente distintas")

In [18]:
str(datetime.datetime.now().strftime("%Y-%m-%d__%H-%M-%S"))
s = '_'
fecha = str(datetime.datetime.now().strftime("%Y-%m-%d__%H-%M-%S_"))
var = str(fecha + "_" + s.join(company_names)+ '.html')
var = var.replace("/","_")

!jupyter nbconvert 2.Portfolio_performance_optimized.ipynb --no-input --output-dir='./html_sin_codigo' --to html --output output.html
!jupyter nbconvert 2.Portfolio_performance_optimized.ipynb --output-dir='./html_con_codigo' --to html --output output.html

os.rename('./html_sin_codigo/output.html', './html_sin_codigo/' + var)
os.rename('./html_con_codigo/output.html','./html_con_codigo/'+ var)

[NbConvertApp] Converting notebook 2.Portfolio_performance_optimized.ipynb to html
[NbConvertApp] Writing 3116996 bytes to ./html_sin_codigo\output.html
[NbConvertApp] Converting notebook 2.Portfolio_performance_optimized.ipynb to html
[NbConvertApp] Writing 3387351 bytes to ./html_con_codigo\output.html
